# <br/>


# Multi-Armed Bandit with Python


# <br/>

Presented by **Robin Allesiardo** from **PJD/Search/AI** (rallesiardo_at_solocal.com)

during **TBD**
![solocal](ressources/foot_solocal.png)

jupyter nbconvert Jupyter "BBL_MAB.ipynb" --to slides

# AB Testing

<img src="ressources/AB.png">


## Definition of the stationnary MAB problem
    
- $K$ **arms**, each associated to a **mean** $\mu^k \in [0,1]$
    

- The **optimal arm** is ${k^*=\arg \max_{k\in K}\mu_k}$ 


- The **optimal mean reward** est ${\mu^* = \max_{k\in K} \mu_k}$


- A **reward** $r_{k_t, t} \in [0,1]$, is drawn from a **distribution of mean** $\mu_k$


In [1]:
from numpy.random import binomial

class MAB:
    def __init__(self, T = 100000, K = 2, delta = 0.1):
        self.T, self.K, self.delta = T, K, delta #horizon, bras, différence avec le bras optimal
        self.mean = [0.5 + (self.delta if i == 0 else 0) for i in range(self.K)]
        """ Caching the reward list """
        self.rewards = [binomial(1, i_mean, int(T)) for i_mean in self.mean]            
        
    def start_game(self):
        """ Move through the game """
        for t in range(int(self.T)):
            self.t = t
            yield int(t)
            
        del self.t
            
    def play(self, k):
        """ Get the reward """
        return self.rewards[k][self.t]

  ## Lower bound on the sample-complexity

The minimal number of samples needed to an alogithm to be $\epsilon$-$\delta$-PAC (Probably Approximately Correct) on a MAB problem is:
  
$$ \Omega \left( \frac{K \text{log}(\frac{1}{\delta})}{\epsilon^2} \right)$$

  $\delta$ has a low impact (it's in the log) but the number of samples needed has a quadratic dependency to $\epsilon$.
      

  ## Pseudo Cumulative Regret
  
  $$R(T) = \sum_{t=0}^{t<T} \mu^* - \mu_{k_t} = \sum_{t=0}^{t<T} \Delta_k$$
      
  #### Trade-off between Exploration and Exploitation?


  ## Lower bound on the cumulative regret


  We know that the mean cumulative regret of any algorithm will be at least
  

  $$ \Omega \left( \frac{K \text{log}(\frac{KT}{\Delta})}{\Delta} \right).$$


  The problem becomes harder as $\Delta$ is smaller.
      

### Confidence intervals are our friends

**Hoeffding Inequality** : The difference between the empirical mean reward of an arm and its mean reward is at most $\epsilon$, with a probability 1-$\delta$; $\epsilon$ being
$$\epsilon = \sqrt{\frac{\text{log}\left(\frac{c t^2}{\delta}\right)}{t}}.$$

**Fun fact**: The empirical mean is an $\epsilon$-$\delta$-PAC estimator.

In [2]:
import math, numpy as np
def get_confidence_bound(t, delta = 0.1, c=1):
    t = t
    return np.sqrt(np.log(c*pow(t,2)/delta)/t)

In [3]:
T = 10000
delta = 0.1
import plotly.offline as pyo
import plotly.express as px
import plotly.graph_objs as go
pyo.init_notebook_mode()

fig = px.line(x=[t for t in range(1, T, 100)], y=[get_confidence_bound(t,delta = delta) for t in range(1, T, 100)],
        line_shape="spline")


In [4]:
fig.show()

# The Random Policy

In [5]:
class RandomBandit():
    
    def __init__(self, K):
        self.K = K
        self.t = 0
        self.counts = [[1] for k in range(K)] # Number of time each arm is played
        self.rewards = [[0] for k in range(K)] # History of rewards
        self.cumulative_reward = [0] # The global cumulative reward
        
    def select(self):
        return np.random.randint(self.K)
    
    def observe(self, k_t, y_t):
        self.t += 1
        self.cumulative_reward.append(self.cumulative_reward[-1]+y_t)
        for k in range(self.K):
            self.counts[k].append(self.counts[k][-1] + (1 if k==k_t else 0))
            self.rewards[k].append(self.rewards[k][-1] + (y_t if k==k_t else 0))

In [6]:
mab = MAB(delta = 0.05)
player = RandomBandit(2)
rewards = []
for i in mab.start_game():
    k = player.select()
    y = mab.play(k)
    player.observe(k,y)
    rewards.append(y)

In [7]:
def mean_reward(player, k = None):
    if k is not None:
        return np.array(player.rewards[k]) / (np.array(player.counts[k])+1)
    else:
        return np.array(player.cumulative_reward) / np.array(list(range(1, len(player.cumulative_reward)+1)))

def get_confidence_bounds(list_of_t):
    return np.array([get_confidence_bound(t) for t in list_of_t])

def get_time(player):
    return np.array(list(range(1, len(player.cumulative_reward)+1)))

In [8]:
empirical_random_rewards = np.cumsum(rewards)/(np.array(range(len(rewards)))+1)
empirical_optimal_rewards = np.cumsum(mab.rewards[0])/(np.array(range(len(rewards)))+1)
empirical_suboptimal_rewards = np.cumsum(mab.rewards[1])/(np.array(range(len(rewards)))+1)

In [9]:
delta = mab.delta
horizon = int(mab.T)
sample = np.linspace(0, horizon-1, 1000).astype(np.int)

def add(i_horizon, fig, k, color, name, interval):
    color_2 = color if color[:4] != "rgba" else color[:-1] + ", 0.01)"
    
    rewards = mean_reward(player, k)
    confidence_bound = get_confidence_bounds(player.counts[k])
    
    fig.add_scatter(x = np.array(range(i_horizon))[sample], y = rewards[:i_horizon][sample], mode='lines', line_color= color[:-1] + ", 1)", name = name)
    if interval:
        fig.add_scatter(x = np.array(range(i_horizon))[sample], y = (rewards[:i_horizon] + confidence_bound[:i_horizon])[sample], mode='lines', line_color=color_2, name = "")
        fig.add_scatter(x = np.array(range(i_horizon))[sample]
                    , y = (rewards[:i_horizon] - confidence_bound[:i_horizon])[sample], mode='lines', fill='tonexty', line_color=color_2, name = "")


In [10]:
def print_at_horizon(i_horizon, interval = True):

    fig = go.Figure()

    fig.update_xaxes(range=[0, i_horizon])
    fig.update_yaxes(range=[0.5-delta, 0.5+2*delta])
    add(i_horizon, fig, 0, 'rgba(255, 0, 0)', "A", interval)
    add(i_horizon, fig, 1, 'rgba(0, 0, 255)', "B", interval)

    # Create scatter trace of text labels
    fig.add_shape(
            # Line Vertical
            go.layout.Shape(
                type="line",
                x0=0,
                y0=0.5,
                x1=i_horizon,
                y1=0.5,
                line=dict(
                    width=1
                )
            )
    )

    fig.add_shape(
            # Line Vertical
            go.layout.Shape(
                type="line",
                name = "mu*",
                x0=0,
                y0=0.5+delta,
                x1=i_horizon,
                y1=0.5+delta,
                line=dict(
                    width=1
                )
            )
    )

    return fig

fig_AB = print_at_horizon((horizon), False)
fig_AB.update_shapes(dict(xref='x', yref='y'))

In [11]:
fig_AB.show()

In [12]:
fig_ABC = print_at_horizon((horizon), True)
fig_ABC.update_shapes(dict(xref='x', yref='y'))

In [13]:
fig_ABC.show()

# Action Elimination

An arm $k$ is eliminated when

$$\hat{\mu}^\text{max} - \hat{\mu}_k > 2\epsilon $$

with
$$\epsilon = \sqrt{\frac{\text{log}\left(\frac{c t^2}{\delta}\right)}{t}}.$$


# UCB: Upper Confidence Bound

**Concept:** Against incertitude, be optimistic.

**Algorithm:** Playing the arm $k$ that maximizes

$$\text{ucb}(k) = \hat{\mu}_k + \sqrt{\frac{2\text{log}(t)}{t_k}}.$$

In [14]:
import math

In [15]:
class UCB():
    
    def __init__(self, K):
        self.K = K
        self.T = 1
        self.t = np.array([1]*K)
        self.mean_rewards = np.array([0.]*K)

        """Visualization Stuff"""
        self.empirical_rewards = [[] for i in range(self.K)]
        self.confidence_bound = [[] for i in range(self.K)]
        
    def _get_ucb(self, k):
        return self.mean_rewards[k] + math.sqrt(2 * math.log(self.T) / self.t[k])
    
    def select(self):
        ucb = [self._get_ucb(i_k) for i_k in range(self.K)]
        max_ = np.argmax(np.array(ucb))
        """Visualization Stuff"""
        for i_k in range(self.K):
            self.empirical_rewards[i_k].append(self.mean_rewards[i_k])
            self.confidence_bound[i_k].append(ucb[i_k])
        return max_
    
    def observe(self, k_t, y_t):
        
        self.mean_rewards[k_t] = float(y_t + self.t[k_t] * self.mean_rewards[k_t]) / float(self.t[k_t]+1)
        self.t[k_t] += 1
        self.T += 1

In [16]:
mab = MAB(delta = 0.05)
player = UCB(2)
rewards = []
played_arm = []
for i in mab.start_game():
    k = player.select()
    y = mab.play(k)
    player.observe(k,y)
    rewards.append(y)
    played_arm.append(k)

In [17]:
import pandas as pd
def get_ratio(list_, what_you_are_looking_for = 0):
    s = pd.Series(list_)
    s = (s == what_you_are_looking_for)
    return s.rolling(5000, min_periods = 1).mean()

optimal_ratio = get_ratio(played_arm, 0)
reward_ratio = get_ratio(rewards, 1)

In [18]:
lines = [
pd.Series(reward_ratio)[sample],
pd.Series(optimal_ratio)[sample],
pd.Series(player.empirical_rewards[0])[sample],
pd.Series(player.empirical_rewards[1])[sample],
pd.Series(player.confidence_bound[0])[sample],
pd.Series(player.confidence_bound[1])[sample]]

names= ["UCB Reward", "Ratio of k^*", "Empirical reward of k^*", "Empirical reward of k^-", "UCB of k^*", "UCB of k^-"]

lines = [go.Scatter(x=i_lines.index[5:],
                             y=i_lines.values[5:], name = names[i]) for i, i_lines in enumerate(lines)]

In [19]:
updatemenus = [dict(
            type="buttons",
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None])])]

layout = go.Layout(title='', xaxis=dict(title='Number of observations'),
                   yaxis=dict(title='Confidence Interval'))#, updatemenus = updatemenus)

fig_ucb = go.Figure(data=lines, layout=layout)

In [20]:
fig_ucb.show()

In [21]:
class TS():
    
    def __init__(self, K, batch = 10):
        self.K = K
        self.T = 1
        self.failure = np.array([1]*K)
        self.success = np.array([1]*K)        
                
        """Visualization Stuff"""
        self.failures = [[1] for i in range(self.K)]
        self.successes = [[1] for i in range(self.K)]
        
    def _draw(self, k):
        return np.random.beta(self.success[k],self.failure[k])
    
    def select(self):
        draw = [self._draw(i_k) for i_k in range(self.K)]
        max_ = np.argmax(np.array(draw))
        return max_
    
    def observe(self, k_t, y_t):
        self.failure[k_t] += 1 - y_t
        self.success[k_t] += y_t

        """Visualization Stuff"""
        for i_k in range(self.K):
            self.failures[i_k].append(self.failure[i_k])
            self.successes[i_k].append(self.success[i_k])

In [22]:
mab = MAB(delta = 0.05)
player = TS(2)
rewards = []
played_arm = []
for i in mab.start_game():
    k = player.select()
    y = mab.play(k)
    player.observe(k,y)
    rewards.append(y)
    played_arm.append(k)

In [23]:
from scipy import stats
import scipy
x = np.linspace(0, 1.0, 100)

def get_y(k, t):
    ks = max(1,player.successes[k][t])
    kf = max(1,player.failures[k][t])
    return [scipy.stats.beta.pdf(i,ks,kf) for i in x]

In [24]:
def get_line(x, y, width = 1.5):
    return go.Scatter(x=x,
                    y=y,
                    mode='lines',
                    line=dict(width=width))

trace1 = get_line(x, get_y(0, 0))
trace2 = get_line(x, get_y(1, 0))

frames = [dict(data= [dict(type='scatter',
                           x=x,
                           y=get_y(0, t)), dict(type='scatter',
                           x=x,
                           y=get_y(1, t))],
               traces= [0, 1],)  #this means that  frames[k]['data'][0]  updates trace1, and   frames[k]['data'][1], trace2 
              for t  in  range(0,1000,10)] 

In [25]:
layout = go.Layout(width=650,
                   height=400,
                   showlegend=False,
                   hovermode='closest',
                   updatemenus=[dict(type='buttons', showactive=False,
                                y=1.05,
                                x=1.15,
                                xanchor='right',
                                yanchor='top',
                                pad=dict(t=0, r=10),
                                buttons=[dict(label='Play',
                                              method='animate',
                                              args=[None, 
                                                    dict(frame=dict(duration=60, 
                                                                    redraw=False),
                                                         transition=dict(duration=0),
                                                         fromcurrent=True,
                                                         mode='immediate')])])])


layout.update(xaxis =dict(range=[0, 1], autorange=False),
              yaxis =dict(range=[0, 20], autorange=False));

ts_distributions = go.Figure(data=[trace1, trace2], frames=frames, layout=layout)

In [26]:
ts_distributions.show()

In [27]:
optimal_ratio = get_ratio(played_arm, 0)
reward_ratio = get_ratio(rewards, 1)

lines = [
pd.Series(reward_ratio)[sample],
pd.Series(optimal_ratio)[sample],
(pd.Series(player.successes[0]) / (pd.Series(player.successes[0]) + pd.Series(player.failures[0])))[sample],
(pd.Series(player.successes[1]) / (pd.Series(player.successes[1]) + pd.Series(player.failures[1])))[sample]]

names= ["TS Reward", "Ratio of k^*", "Empirical reward of k^*", "Empirical reward of k^-"]

lines = [go.Scatter(x=i_lines.index[5:20000],
                             y=i_lines.values[5:20000], name = names[i]) for i, i_lines in enumerate(lines)]


In [28]:
updatemenus = [dict(
            type="buttons",
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None])])]

layout = go.Layout(title='', xaxis=dict(title='Number of observations'),
                   yaxis=dict(title='Estimators'))#, updatemenus = updatemenus)

fig_ts = go.Figure(data=lines, layout=layout)

In [29]:
fig_ts.show()

# Non-Stationnary Bandits

The mean $\mu_{k,t}$ changes during the run.

Classic algorithms do not provide guarantee against non-stationnarity.


# Algorithms dealing with non-stationnarity

- **SER3** (Successive Elimination with Random Round-Robin)
    - Assumption of positive mean gap $\Delta_t$
    - Regret of $\frac{K \text{log}(T)}{\min_t{\Delta_t}}$
- **SW-UCB** (Sliding Window UCB)
    - Piecewise stationary
    - Regret of $\sqrt{KT}$ (optimal on non-stationnary MAB)
- **EXP3**
    - Adversarial rewards
    - Randomization against adversity
    - Regret of $\sqrt{KT}$

# Contextual Bandits

Rewards depend on context.

**Several family of problems**:

- **Each arm is a context**
    - ($x_0, ..., x_k, ..., x_K$)
    - Contexts allows to generalize rewards between arms
    - e.g. : Finding the best hyper-parametrization of an algorithm
- **The context change at each iteration and the reward depends on contexts**
    - ($x_0, ..., x_t, ..., x_T$)
    - e.g. : User of a website are contexts, ads are arms.
- **Hybrid**
    - e.g. : A context at each timestep (a query...) and arms with associated contexts (a result list...)ntenus)

#  Contextual Bandits

- **State Based Contextual Bandit**
    - Contexts are mapped to states
    - One MAB algorithm by state
- **LinUCB**
    - Linear model with UCB
- **Contextual Thompson Sampling**
    - Scores sampled from a multivariate distribution centered with a liean model
- **$\gamma$-Greedy**
    - Exploration with a $\gamma$ probability, else exploitation with a model trained only with samples gathered during exploration
- **BanditForest**
    - Pure exploration until the elimination of the non-optimal splitting criterion then Successive Elimination in the leafs.
